In [1]:
import numpy as np
import matplotlib.pyplot as plt
import math

G = 6.6743015e-11
Eps0 = 8.8541878128e-12

class Particle:
    def __init__(self, position, inertia: (float, float, float), mass, charge : float):
        self.position = np.array(position)
        self.inertia = np.array(inertia)
        self.mass = mass
        self.charge = charge

    def distance(self, p: "Particle"):
        return np.sum((self.position-p.position)**2)
        
    def force(self, p) -> float:
        ds = self.distance(p)
        Fg = G * self.mass * p.mass / ds
        Fc = self.charge * p.charge / (4 * math.pi * Eps0 * ds)
        return Fg - Fc
    
    def forceV(self, p) -> np.ndarray:
        diff = p.position-self.position
        length = np.linalg.norm(diff)
        return (diff/length)*self.force(p)
        
    def move(self, t: float):
        self.position = self.position + (self.inertia / self.mass) * t 
        
    def apply_force_primitive(self, f: np.ndarray, t: float):
        self.inertia = self.inertia + f*t
        self.move(t)

    def apply_force_first_diff(self, f: np.ndarray, t: float):
        self.move(t)
        i = (f*(t**2))/(self.mass)
        self.position = self.position + i
        self.inertia = self.inertia + f*t

class System:
    def __init__(self, particles: [Particle], t: float):
        self.t = t
        self.particles = particles
        
    def primitive_step(self):
        forces = np.zeros((len(self.particles), 3))
        for i in range(0, len(self.particles)):
            p1 = self.particles[i]
            for j in range(i+1, len(self.particles)):
                p2 = self.particles[j]
                f = p1.forceV(p2)
                forces[i] = forces[i] + f
                forces[j] = forces[j] - f
        
            p1.apply_force_primitive(forces[i], self.t)
            self.particles[i] = p1

    def first_diff_step(self):
        forces = np.zeros((len(self.particles), 3))
        for i in range(0, len(self.particles)):
            p1 = self.particles[i]
            for j in range(i+1, len(self.particles)):
                p2 = self.particles[j]
                f = p1.forceV(p2)
                forces[i] = forces[i] + f
                forces[j] = forces[j] - f

            p1.apply_force_first_diff(forces[i], self.t)
            self.particles[i] = p1
                

In [2]:
from dataclasses import dataclass
from typing import Tuple
import numpy as np
import matplotlib.pyplot as plt
import math

from matplotlib import animation
from IPython.display import HTML

@dataclass
class Points:
    masses: np.array
    positions: np.array
    inertias: np.array

@dataclass
class Links:
    starts: np.array
    ends: np.array
    lengths: np.array
    sconstants: np.array
    dconstants: np.array
        
class ElasticBody():
    def __init__(self, points, links, bbox, dt, gforce=(0,0,0), gresist=0):
        self.points = points
        self.links = links
        self.bbox = bbox
        self.dt = dt
        self.gforce = gforce
        self.gresist = gresist
       
    def movePoints(self):
        self.points.positions += self.points.inertias * self.dt/self.points.masses[:, np.newaxis]

    def applyForces(self, forces):
        self.points.inertias += forces * self.dt

    def forces(self):
        forces = np.zeros_like(self.points.inertias)

        # Springs
        diffpositions = self.points.positions[tuple(self.links.ends), :] - self.points.positions[tuple(self.links.starts), :]
        lengths = np.linalg.norm(diffpositions, axis=1)
        directions = diffpositions/lengths[:, np.newaxis]

        springforces = (self.links.lengths - lengths) * self.links.sconstants
        sfv = springforces[:, np.newaxis]*directions

        # Dampers
        vs = self.points.inertias/self.points.masses[:, np.newaxis]
        diffvelocities = vs[tuple(self.links.ends), :] - vs[tuple(self.links.starts), :]
        velocitiesalongdampers = np.sum(diffvelocities*directions, axis=1)
        
        damperforces = velocitiesalongdampers * self.links.dconstants
        dfv = damperforces[:, np.newaxis]*directions

        forces[tuple(self.links.starts), :] += dfv - sfv
        forces[tuple(self.links.ends), :] += sfv - dfv
        
        #gravity
        #exclude points with infinite mass
        ms = np.copy(self.points.masses)
        ms[self.points.masses == math.inf] = 0
        forces += self.gforce * ms[:, np.newaxis]
        
        return forces

    def contain(self):
        contained = np.clip(self.points.positions, a_min=self.bbox[::2], a_max=self.bbox[1::2])
        clamped = self.points.positions - contained
        self.points.inertias[clamped != 0.0] = 0.0
        self.points.positions = contained
        
    def step(self):
        self.applyForces(self.forces())
        self.points.inertias *= (1-self.gresist)**self.dt
        self.movePoints()
        self.contain()

    def animate(self, nframes):
        self.fig = plt.figure(figsize=(5,5))
        self.ax = plt.subplot(1,1,1)   
        self.ax.set_xlim((self.bbox[0], self.bbox[1]))  
        self.ax.set_ylim((self.bbox[2], self.bbox[3]))  
        lines = []
        
        for si, ei in zip(self.links.starts, self.links.ends):
            ps = self.points.positions[si]
            pe = self.points.positions[ei]
            xs = [ps[0], pe[0]]
            ys = [ps[1], pe[1]]
            zs = [ps[2], pe[2]]
            l = self.ax.plot(xs, ys)[0]
            lines.append(l)

        plt.close()
            
        def drawFrame(n):
            self.step()
            for i, (si, ei) in enumerate(zip(self.links.starts, self.links.ends)):
                ps = self.points.positions[si]
                pe = self.points.positions[ei]
                xs = [ps[0], pe[0]]
                ys = [ps[1], pe[1]]
                zs = [ps[2], pe[2]]
                lines[i].set_data((xs, ys))
            return lines
            
        anim = animation.FuncAnimation(self.fig, drawFrame, frames=nframes, interval=20, blit=True)
        return HTML(anim.to_jshtml())

In [10]:
# falling box test
box = (-3, 3, -3, 3, 0, 0)
points = Points(
    masses=np.array([1,1,1,1]),
    positions=np.array([
        (0,0,0),
        (1,0,0),
        (1,1,0),
        (0,1,0)
    ]).astype(float),
    inertias=np.array([
        (0,0,0),
        (0,0,0),
        (0,0,0),
        (0,0,0)
    ]).astype(float),
)
links = Links(
    starts=np.array([0,1,2,3,0,1]),
    ends=np.array([1,2,3,0,2,3]),
    lengths=np.array([1,1,1,1,1.41,1.41]).astype(float),
    sconstants=np.array([20,20,20,20,20,20]).astype(float),
    dconstants=np.array([5,5,5,5,5,5]).astype(float)
)

saj = ElasticBody(points=points, links=links, bbox=box, dt=0.05, gforce=(0, -0.1, 0))
saj.animate(400)

In [4]:
box = (-3, 3, -3, 3, -3, 3)
center = PointMass(10, (0, 0, 0), (0, 0, 0))
wing1 = PointMass(4, (1, -1, 0), (0, 0, -0.33))
wing2 = PointMass(4, (1, 1, 0), (0, 0, 0.3))

sc1 = Spring(center, wing1, 20, math.sqrt(2))
sc2 = Spring(center, wing2, 20, math.sqrt(2))
s12 = Spring(wing1, wing2, 20, 2)
wingnut = ElasticBody(joints=[center, wing1, wing2], springs=[sc1, sc2, s12], dampers=[], bbox=box, dt=0.5)
wingnut.animate(400)

NameError: name 'PointMass' is not defined

In [ ]:
#Damper test
p1 = PointMass(math.inf, (-1, 0, 0), (0, 0, 0))
p2 = PointMass(1, (-1, -1, 0), (0, 0, 0))
s1 = Spring(p1, p2, 5, 1.5)

p3 = PointMass(math.inf, (0, 0, 0), (0, 0, 0))
p4 = PointMass(1, (0, -1, 0), (0, 0, 0))
s2 = Spring(p3, p4, 5, 1.2)

p5 = PointMass(math.inf, (1, 0, 0), (0, 0, 0))
p6 = PointMass(1, (1, -1, 0), (0, 0, 0))
s3 = Spring(p5, p6, 5, 1.5)
d1 = Damper(p5, p6, 1)
saj = ElasticBody(springs=[s1, s2, s3], dampers=[d1], joints=[p1, p2, p3, p4, p5, p6], bbox=box, dt=0.1)
saj.animate(200)

In [5]:
# double pendulum
orig = PointMass(math.inf, (0, 0, 0), (0, 0, 0))
p1 = PointMass(1, (1, 0, 0), (0, 0, 0))
s1 = Spring(orig, p1, 20, 1)
d1 = Damper(orig, p1, 6)
p2 = PointMass(1, (1, 1, 0), (0, 0, 0))
s2 = Spring(p1, p2, 20, 1)
d2 = Damper(p1, p2, 6)

dp = ElasticBody(joints=[orig, p1, p2], springs=[s1, s2], dampers=[d1,d2], bbox=box, dt=0.10, gforce=(0, -0.1, 0), gresist=-0.01)
dp.animate(400)

NameError: name 'PointMass' is not defined

In [ ]:
#bridge
bbox = (-6, 6, 0, 12, 0, 0)
uarc = []
larc = []
ua = 0.15
la = 0.12
ribbons = []
dampers = []
for i in range (-5, 6):
    uarc.append(PointMass(1, (i,5-ua*i**2,0), (0,0,0)))
    larc.append(PointMass(1, (i,3-la*i**2,0), (0,0,0)))

l = larc[0].distanceTo(uarc[0])
ribbons.append(Spring(larc[0], uarc[0], 60, l))
dampers.append(Damper(larc[0], uarc[0], 10))
for i in range(1, len(uarc)):
    p1 = uarc[i-1]
    p2 = uarc[i]
    l1 = p1.distanceTo(p2)
    p3 = larc[i-1]
    p4 = larc[i]
    l2 = p3.distanceTo(p4)
    ribbons.append(Spring(p1, p2, 60, l1))
    dampers.append(Damper(p1, p2, 10))
    ribbons.append(Spring(p3, p4, 60, l2))
    dampers.append(Damper(p3, p4, 10))

    l3 = p1.distanceTo(p4)
    ribbons.append(Spring(p1, p4, 60, l3))
    dampers.append(Damper(p1, p4, 10))
    l4 = p4.distanceTo(p2)
    ribbons.append(Spring(p4, p2, 60, l4))
    dampers.append(Damper(p4, p2, 10))
    l5 = p3.distanceTo(p2)
    ribbons.append(Spring(p3, p2, 60, l5))
    dampers.append(Damper(p3, p2, 10))
    
uarc.extend(larc)
bridge = ElasticBody(joints=uarc, springs=ribbons, dampers=dampers, bbox=bbox, dt=0.05, gforce=(0,-0.1,0))
bridge.animate(400)

In [ ]:
ps = Points(np.array([math.inf, 1, 1]), np.array([[0,0,0],[1, 0, 0], [1, 1, 0]]).astype(float), np.zeros((3,3), dtype=float))
ls = Links(
    np.array([0, 1]),
    np.array([1, 2]),
    np.array([1,1]),
    np.array([20,20]),
    np.array([6,6])
)

ep = npElasticBody(points=ps, links=ls, bbox=box, dt=0.1, gforce=(0, -0.1, 0), gresist=-0.01)
ep.animate(400)